# Objectives {.unnumbered}

By the end of this lab, you will:
1. Load and analyze the **Lightcast dataset** in **Spark DataFrame**.
2. Create **five easy and three medium-complexity visualizations** using **Plotly**.
3. Explore **salary distributions, employment trends, and job postings**.
4. Analyze **skills in relation to NAICS/SOC/ONET codes and salaries**.
5. Customize **colors, fonts, and styles** in all visualizations (**default themes result in a 2.5-point deduction**).
6. Follow **best practices for reporting on data communication**.

# Step 1: Load the Dataset {.unnumbered}


In [4]:
import pandas as pd
import plotly.express as px
import plotly.io as pio
pio.renderers.default = "vscode"
from pyspark.sql import SparkSession
from pyspark.sql.functions import col


# Initialize Spark Session
spark = SparkSession.builder.appName("LightcastData").getOrCreate()

# Load Data
df = spark.read.option("header", "true").option("inferSchema", "true").option("multiLine","true").option("escape", "\"").csv("./data/lightcast_job_postings.csv")

# Show Schema and Sample Data
df.printSchema()
df.show(5)


Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
25/03/26 03:22:45 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
25/03/26 03:22:46 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.


root
 |-- ID: string (nullable = true)
 |-- LAST_UPDATED_DATE: date (nullable = true)
 |-- LAST_UPDATED_TIMESTAMP: timestamp (nullable = true)
 |-- DUPLICATES: integer (nullable = true)
 |-- POSTED: date (nullable = true)
 |-- EXPIRED: date (nullable = true)
 |-- DURATION: integer (nullable = true)
 |-- SOURCE_TYPES: string (nullable = true)
 |-- SOURCES: string (nullable = true)
 |-- URL: string (nullable = true)
 |-- ACTIVE_URLS: string (nullable = true)
 |-- ACTIVE_SOURCES_INFO: string (nullable = true)
 |-- TITLE_RAW: string (nullable = true)
 |-- BODY: string (nullable = true)
 |-- MODELED_EXPIRED: date (nullable = true)
 |-- MODELED_DURATION: integer (nullable = true)
 |-- COMPANY: integer (nullable = true)
 |-- COMPANY_NAME: string (nullable = true)
 |-- COMPANY_RAW: string (nullable = true)
 |-- COMPANY_IS_STAFFING: boolean (nullable = true)
 |-- EDUCATION_LEVELS: string (nullable = true)
 |-- EDUCATION_LEVELS_NAME: string (nullable = true)
 |-- MIN_EDULEVELS: integer (nullable

25/03/26 03:23:02 WARN SparkStringUtils: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


+--------------------+-----------------+----------------------+----------+----------+----------+--------+--------------------+--------------------+--------------------+-----------+-------------------+--------------------+--------------------+---------------+----------------+--------+--------------------+-----------+-------------------+----------------+---------------------+-------------+-------------------+-------------+------------------+---------------+--------------------+--------------------+--------------------+-------------+------+-----------+----------------+-------------------+---------+-----------+--------------------+--------------------+-------------+------+--------------+-----+--------------------+-----+----------+---------------+--------------------+---------------+--------------------+------------+--------------------+------------+--------------------+------+--------------------+------+--------------------+------+--------------------+------+--------------------+------+---

# Salary Distribution by Employment Type
- Identify salary trends across different employment types.
- **Filter the dataset**
  - Remove records where **salary is missing or zero**.
- **Aggregate Data**
  - Group by **employment type** and compute salary distribution.
- **Visualize results**
  - Create a **box plot** where:
    - **X-axis** = `EMPLOYMENT_TYPE_NAME`
    - **Y-axis** = `SALARY_FROM`
  - Customize **colors, fonts, and styles** to avoid a **2.5-point deduction**.
- **Explanation:** Write two sentences about what the graph reveals.



In [5]:
# Your Code for 1st question here
pdf = df.select("EMPLOYMENT_TYPE_NAME", "SALARY").toPandas()
fig = px.box(pdf, x="EMPLOYMENT_TYPE_NAME", y="SALARY", title="Salary Distribution by Employment Type", color_discrete_sequence=["#636EFA"])
fig.update_layout(font_family="Arial", title_font_size=16)
fig.show()

# Salary Distribution by Industry
- Compare salary variations across industries.
- **Filter the dataset**
  - Keep records where **salary is greater than zero**.
- **Aggregate Data**
  - Group by **NAICS industry codes**.
- **Visualize results**
  - Create a **box plot** where:
    - **X-axis** = `NAICS2_NAME`
    - **Y-axis** = `SALARY_FROM`
  - Customize colors, fonts, and styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [6]:
# Your code for 2nd question here

pdf = df.select("NAICS2_NAME", "SALARY_FROM").toPandas()
fig = px.box(pdf, x="NAICS2_NAME", y="SALARY_FROM", title=" Salary Distribution by Industry", color_discrete_sequence=["#636EFA"])
fig.update_layout(font_family="Arial", title_font_size=16)
fig.show()

In [7]:
pdf = df.select("NAICS2_NAME", "SALARY_FROM").toPandas()

# Compute average salary by industry
avg_salary = pdf.groupby("NAICS2_NAME", as_index=False)["SALARY_FROM"].mean()

# Create a bar chart using Plotly
fig = px.bar(avg_salary, 
             x="NAICS2_NAME", 
             y="SALARY_FROM", 
             title="Average Salary by Industry", 
             color_discrete_sequence=["#636EFA"])

# Customize layout
fig.update_layout(font_family="Arial", title_font_size=16, 
                  xaxis_title="Industry", 
                  yaxis_title="Average Salary (USD)", 
                  xaxis_tickangle=-45)

fig.show()


# Job Posting Trends Over Time
- Analyze how job postings fluctuate over time.
- **Aggregate Data**
  - Count job postings per **posted date (`POSTED`)**.
- **Visualize results**
  - Create a **line chart** where:
    - **X-axis** = `POSTED`
    - **Y-axis** = `Number of Job Postings`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [8]:
# Convert Spark DataFrame to Pandas DataFrame
pdf = df.select("POSTED").toPandas()

# Convert 'POSTED' column to datetime
pdf["POSTED"] = pd.to_datetime(pdf["POSTED"])

# Aggregate: Count job postings per posted date
job_posting_trends = pdf.groupby("POSTED").size().reset_index(name="Job Postings")

# Create line chart
fig = px.line(job_posting_trends, 
              x="POSTED", 
              y="Job Postings", 
              title="Job Posting Trends Over Time", 
              line_shape="linear", 
              color_discrete_sequence=["#636EFA"])

# Customize layout
fig.update_layout(font_family="Arial", title_font_size=16,
                  xaxis_title="Date Posted", 
                  yaxis_title="Number of Job Postings", 
                  xaxis_tickangle=-45)

fig.show()

# Top 10 Job Titles by Count
- Identify the most frequently posted job titles.
- **Aggregate Data**
  - Count the occurrences of each **job title (`TITLE_NAME`)**.
  - Select the **top 10 most frequent titles**.
- **Visualize results**
  - Create a **bar chart** where:
    - **X-axis** = `TITLE_NAME`
    - **Y-axis** = `Job Count`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [9]:
# Your code for 4th question here
# Convert Spark DataFrame to Pandas DataFrame
pdf = df.select("TITLE_NAME").toPandas()

# Aggregate: Count occurrences of each job title
job_title_counts = pdf["TITLE_NAME"].value_counts().reset_index()
job_title_counts.columns = ["TITLE_NAME", "Job Count"]

# Select the top 10 most frequent job titles
top_10_jobs = job_title_counts.head(10)

# Create a horizontal bar chart
fig = px.bar(top_10_jobs, 
             x="Job Count", 
             y="TITLE_NAME", 
             orientation="h", 
             title="Top 10 Job Titles by Count",
             color_discrete_sequence=["#636EFA"])

# Customize layout
fig.update_layout(font_family="Arial", title_font_size=16,
                  xaxis_title="Number of Job Postings", 
                  yaxis_title="Job Title", 
                  yaxis=dict(autorange="reversed"))  # Reverse y-axis for ranking order

fig.show()

# Remote vs On-Site Job Postings
- Compare the proportion of remote and on-site job postings.
- **Aggregate Data**
  - Count job postings by **remote type (`REMOTE_TYPE_NAME`)**.
- **Visualize results**
  - Create a **pie chart** where:
    - **Labels** = `REMOTE_TYPE_NAME`
    - **Values** = `Job Count`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [10]:
# Your code for 5th question here
# Convert Spark DataFrame to Pandas DataFrame
pdf = df.select("REMOTE_TYPE_NAME").toPandas()

# Aggregate: Count occurrences of each remote type
remote_type_counts = pdf["REMOTE_TYPE_NAME"].value_counts().reset_index()
remote_type_counts.columns = ["REMOTE_TYPE_NAME", "Job Count"]

# Create a pie chart
fig = px.pie(remote_type_counts, 
             names="REMOTE_TYPE_NAME", 
             values="Job Count", 
             title="Remote vs On-Site Job Postings",
             color_discrete_sequence=px.colors.qualitative.Set2)  # Custom color palette

# Customize layout
fig.update_layout(font_family="Arial", title_font_size=16)

fig.show()

# Skill Demand Analysis by Industry (Stacked Bar Chart)
- Identify which skills are most in demand in various industries.
- **Aggregate Data**
  - Extract **skills** from job postings.
  - Count occurrences of skills grouped by **NAICS industry codes**.
- **Visualize results**
  - Create a **stacked bar chart** where:
    - **X-axis** = `Industry`
    - **Y-axis** = `Skill Count`
    - **Color** = `Skill`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [11]:
print(df.columns)

['ID', 'LAST_UPDATED_DATE', 'LAST_UPDATED_TIMESTAMP', 'DUPLICATES', 'POSTED', 'EXPIRED', 'DURATION', 'SOURCE_TYPES', 'SOURCES', 'URL', 'ACTIVE_URLS', 'ACTIVE_SOURCES_INFO', 'TITLE_RAW', 'BODY', 'MODELED_EXPIRED', 'MODELED_DURATION', 'COMPANY', 'COMPANY_NAME', 'COMPANY_RAW', 'COMPANY_IS_STAFFING', 'EDUCATION_LEVELS', 'EDUCATION_LEVELS_NAME', 'MIN_EDULEVELS', 'MIN_EDULEVELS_NAME', 'MAX_EDULEVELS', 'MAX_EDULEVELS_NAME', 'EMPLOYMENT_TYPE', 'EMPLOYMENT_TYPE_NAME', 'MIN_YEARS_EXPERIENCE', 'MAX_YEARS_EXPERIENCE', 'IS_INTERNSHIP', 'SALARY', 'REMOTE_TYPE', 'REMOTE_TYPE_NAME', 'ORIGINAL_PAY_PERIOD', 'SALARY_TO', 'SALARY_FROM', 'LOCATION', 'CITY', 'CITY_NAME', 'COUNTY', 'COUNTY_NAME', 'MSA', 'MSA_NAME', 'STATE', 'STATE_NAME', 'COUNTY_OUTGOING', 'COUNTY_NAME_OUTGOING', 'COUNTY_INCOMING', 'COUNTY_NAME_INCOMING', 'MSA_OUTGOING', 'MSA_NAME_OUTGOING', 'MSA_INCOMING', 'MSA_NAME_INCOMING', 'NAICS2', 'NAICS2_NAME', 'NAICS3', 'NAICS3_NAME', 'NAICS4', 'NAICS4_NAME', 'NAICS5', 'NAICS5_NAME', 'NAICS6', 'NAIC

In [ ]:
# Your code for 6th question here
import pandas as pd
import plotly.express as px

# Convert Spark DataFrame to Pandas
pdf = df.select("NAICS2_NAME", "SKILLS_NAME").toPandas()

# Ensure correct column names exist
print(pdf.columns)  

# Drop missing values in the SKILLS_NAME column
pdf = pdf.dropna(subset=["SKILLS_NAME"])

# Convert columns to string (if necessary)
pdf["NAICS2_NAME"] = pdf["NAICS2_NAME"].astype(str)
pdf["SKILLS_NAME"] = pdf["SKILLS_NAME"].astype(str)

# Aggregate: Count occurrences of each skill within industries
skill_counts = pdf.groupby(["NAICS2_NAME", "SKILLS_NAME"]).size().reset_index(name="Skill Count")

# Check if data is properly grouped
print(skill_counts.head())

# Create stacked bar chart
fig = px.bar(skill_counts, 
             x="NAICS2_NAME", 
             y="Skill Count", 
             color="SKILLS_NAME", 
             title="Skill Demand Analysis by Industry",
             barmode="stack",  # Stacked bars
             color_discrete_sequence=px.colors.qualitative.Set3)  # Custom color scheme

# Customize layout
fig.update_layout(font_family="Arial", title_font_size=16,
                  xaxis_title="Industry", 
                  yaxis_title="Skill Count",
                  xaxis_tickangle=-45, 
                  legend_title="Skill")

fig.show()


Index(['NAICS2_NAME', 'SKILLS_NAME'], dtype='object')
                       NAICS2_NAME  \
0  Accommodation and Food Services   
1  Accommodation and Food Services   
2  Accommodation and Food Services   
3  Accommodation and Food Services   
4  Accommodation and Food Services   

                                         SKILLS_NAME  Skill Count  
0  [\n  "Ability To Meet Deadlines",\n  "Manageme...            1  
1  [\n  "Agile Methodology",\n  "Operations",\n  ...            1  
2  [\n  "Agile Methodology",\n  "Requirements Eli...            1  
3  [\n  "Angular (Web Framework)",\n  "Presentati...            1  
4  [\n  "Animal Health",\n  "Marketing Operations...            1  



# Salary Analysis by ONET Occupation Type (Bubble Chart)
- Analyze how salaries differ across ONET occupation types.
- **Aggregate Data**
  - Compute **median salary** for each occupation in the **ONET taxonomy**.
- **Visualize results**
  - Create a **bubble chart** where:
    - **X-axis** = `ONET_NAME`
    - **Y-axis** = `Median Salary`
    - **Size** = Number of job postings
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [ ]:
# Your code for 7th question here

# Convert Spark DataFrame to Pandas DataFrame
pdf = df.select("ONET_NAME", "SALARY_FROM").toPandas()

# Remove rows with missing salary values
pdf = pdf.dropna(subset=["SALARY_FROM"])

# Aggregate: Compute median salary & job posting count per ONET occupation
salary_analysis = pdf.groupby("ONET_NAME").agg(
    Median_Salary=("SALARY_FROM", "median"), 
    Job_Postings=("ONET_NAME", "count")
).reset_index()

# Create bubble chart
fig = px.scatter(salary_analysis, 
                 x="ONET_NAME", 
                 y="Median_Salary", 
                 size="Job_Postings", 
                 title="Salary Analysis by ONET Occupation Type", 
                 color="Median_Salary", 
                 color_continuous_scale="Blues")  # Custom color scale

# Customize layout
fig.update_layout(font_family="Arial", title_font_size=16,
                  xaxis_title="ONET Occupation", 
                  yaxis_title="Median Salary (USD)", 
                  xaxis_tickangle=-45)

fig.show()

# Career Pathway Trends (Sankey Diagram)
- Visualize job transitions between different occupation levels.
- **Aggregate Data**
  - Identify career transitions between **SOC job classifications**.
- **Visualize results**
  - Create a **Sankey diagram** where:
    - **Source** = `SOC_2021_2_NAME`
    - **Target** = `SOC_2021_3_NAME`
    - **Value** = Number of transitions
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [13]:
# Your code for 8th question here
import pandas as pd
import plotly.graph_objects as go

# Load Data
df = spark.read.option("header", "true").option("inferSchema", "true").option("multiLine","true").option("escape", "\"").csv("./data/lightcast_job_postings.csv")

# Show Schema and Sample Data
df.printSchema()
# Convert Spark DataFrame to Pandas DataFrame
pdf = df.select("SOC_2021_2_NAME", "SOC_2021_3_NAME").toPandas()

# Aggregate: Count the number of transitions between occupation levels
transition_counts = pdf.groupby(["SOC_2021_2_NAME", "SOC_2021_3_NAME"]).size().reset_index(name="Value")

# Create lists for Sankey diagram
source_labels = transition_counts["SOC_2021_2_NAME"].tolist()
target_labels = transition_counts["SOC_2021_3_NAME"].tolist()
values = transition_counts["Value"].tolist()

# Combine unique labels for indexing
all_labels = list(set(source_labels + target_labels))
label_indices = {label: i for i, label in enumerate(all_labels)}

# Map source and target labels to numeric indices
source_indices = [label_indices[label] for label in source_labels]
target_indices = [label_indices[label] for label in target_labels]

# Create Sankey diagram
fig = go.Figure(go.Sankey(
    node=dict(
        pad=15,
        thickness=20,
        line=dict(color="black", width=0.5),
        label=all_labels,  # Labels for nodes
        color="lightblue"
    ),
    link=dict(
        source=source_indices,  # Source indices
        target=target_indices,  # Target indices
        value=values  # Number of transitions
    )
))

# Customize layout
fig.update_layout(title_text="Career Pathway Trends (Sankey Diagram)", font_size=12)

fig.show()

root
 |-- ID: string (nullable = true)
 |-- LAST_UPDATED_DATE: date (nullable = true)
 |-- LAST_UPDATED_TIMESTAMP: timestamp (nullable = true)
 |-- DUPLICATES: integer (nullable = true)
 |-- POSTED: date (nullable = true)
 |-- EXPIRED: date (nullable = true)
 |-- DURATION: integer (nullable = true)
 |-- SOURCE_TYPES: string (nullable = true)
 |-- SOURCES: string (nullable = true)
 |-- URL: string (nullable = true)
 |-- ACTIVE_URLS: string (nullable = true)
 |-- ACTIVE_SOURCES_INFO: string (nullable = true)
 |-- TITLE_RAW: string (nullable = true)
 |-- BODY: string (nullable = true)
 |-- MODELED_EXPIRED: date (nullable = true)
 |-- MODELED_DURATION: integer (nullable = true)
 |-- COMPANY: integer (nullable = true)
 |-- COMPANY_NAME: string (nullable = true)
 |-- COMPANY_RAW: string (nullable = true)
 |-- COMPANY_IS_STAFFING: boolean (nullable = true)
 |-- EDUCATION_LEVELS: string (nullable = true)
 |-- EDUCATION_LEVELS_NAME: string (nullable = true)
 |-- MIN_EDULEVELS: integer (nullable